# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction/Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction/Business Problem <a name="introduction"></a>

In this project we will identify **neighborhoods in Toronto, Canada and New York City, USA that fit** the international **expansion** strategy **for an upscale Italian restaurant chain based in Milan, Italy.**  The primary focus of this strategy is to **identify neighborhoods that have a similar commercial venue profile to the Milan neighborhoods** that the chain and other Italian resturants currently operate in. 

Following **this strategy** offers several benefits to the chain as it seeks to establish a presence on the east coast of North America.  It **reduces the learning curve of operating in new countries by reducing the unknowns.**  The country will still be unfamiliar however the neighborhood profiles will be familiar and more normal to operate in.  In addition, by identifying neighborhoods that already support Italian restaurants, the chain will be able to **benefit from the "second mover" advantage** as it is already established that Italian restaurants can be successful there.  

The neighborhoods that are identified in this project will be utilized to support future expansion decisions by the chain.  The stakeholders who will benefit the most from this project are the members of the chain's management team that has been tasked with North America expansion.

## Data <a name="data"></a>

To successfully complete this project, it will be neccessary to identify:
* Neighborhood names and commercial venue profiles of Milan neighborhoods where Italian restaurants are successful
* Neighborhood names and commercial venue profiles of similar Toronto and New York City neighborhoods

The raw data neccessary to complete these tasks will be identified and scraped from across the internet.  Since this will be a comprehensive analysis that covers all neighborhoods of the three cities, it will require a large amount of raw data that will consume the single computer resources available for wrangling and processing.  To make the work manageable, it was decided to segment the work for each of the individual cities as much as possible then to concatenate the data for the final analysis.

The **Milan** borough and neighborhood names were web scraped utilizing Beautiful Soup from the Wikipedia web page: [Municipalities_of_Milan](https://en.wikipedia.org/wiki/Municipalities_of_Milan).  This data was wrangled into the proper format then geopy was utilized to obtain the geospatial coordinates for each neighborhood.  This information was then passed to the Foursquare API which provided the top 100 venues within a 500 meter radius from the geospatial coordinates of each of the 134 neighborhoods of Milan.  After further data wrangling, this data was then ready to be analyzed.

The **Toronto** borough and neighborhood names along with their corresponding geospatial coordinates were obtained from a previous project in this course.  It is noted that the previous project on Toronto limited the neighborhoods to only those containing "Toronto" in the name whereas this report covers all Toronto neighborhoods thus additional data mining was required.  This data was wrangled into the proper format then passed to the Foursquare API which provided the top 100 venues within a 500 meter radius from the geospatial coordinates of each of the 103 neighborhoods of Toronto.  After further data wrangling, this data was then ready to be analyzed.

The **New York City** borough and neighborhood names along with their corresponding geospatial coordinates were obtained from a previous project in this course.  It is noted that the previous project on New York City limited the neighborhoods to only those in the Manhattan borough whereas this report covers all New York City neighborhoods in all five boroughs thus additional data mining was required.  This data was wrangled into the proper format then passed to the Foursquare API which provided the top 100 venues within a 500 meter radius from the geospatial coordinates of each of the 306 neighborhoods of New York City.  After further data wrangling, this data was then ready to be analyzed.

### Notebook Preparation

Importing the libraries and modules neccessary to complete this project

In [2]:
import requests
import urllib.request
import time
from bs4 import BeautifulSoup

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score

import folium # map rendering library

import wget

import geopy
from geopy.extra.rate_limiter import RateLimiter
from geopy.geocoders import Nominatim

from urllib.request import urlopen

from collections import Counter

print('Libraries imported.')


Libraries imported.


### Milan, Italy

In [1]:
url = 'https://en.wikipedia.org/wiki/Municipalities_of_Milan'

In [3]:
html = urlopen(url)

In [4]:
soup = BeautifulSoup(html, 'html.parser')

In [5]:
table =soup.select('table')[-2]

In [6]:
#Create array to hold the data we extract
boroughs = []
neighborhoods = []

rows = table.find_all('tr')

for row in rows:
    cells = row.find_all('td')
        
        
    if len(cells) > 1:
        borough = cells[1]
        boroughs.append(borough.text.strip())
            
        neighborhood = cells[5]
        neighborhoods.append(neighborhood.text.strip())

# for table in tables:
    # rows = table.find_all('tr')
    
    # for row in rows:
        # cells = row.find_all('td')
        
        
        # if len(cells) > 1:
            # borough = cells[1]
            # boroughs.append(borough.text.strip())
            
            # neighborhood = cells[5]
            # neighborhoods.append(neighborhood.text.strip())

In [7]:
ml_df1 = pd.DataFrame(boroughs, columns = ['Borough'])
ml_df1['Neighborhood'] = neighborhoods

print(ml_df1.shape)
ml_df1.head(10)

(9, 2)


Borough  \
0                                     Centro storico   
1  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
2               Città Studi, Lambrate, Porta Venezia   
3                          Porta Vittoria, Forlanini   
4                Vigentino, Chiaravalle, Gratosoglio   
5                                Barona, Lorenteggio   
6                        Baggio, De Angeli, San Siro   
7                 Fiera, Gallaratese, Quarto Oggiaro   
8                          Porta Garibaldi, Niguarda   

                                        Neighborhood  
0  Brera, Centro Storico, Conca del Naviglio, Gua...  
1  Adriano, Crescenzago, Gorla, Greco, Loreto, Ma...  
2  Casoretto, Cimiano, Città Studi, Dosso, Lambra...  
3  Acquabella, Calvairate, Castagnedo, Cavriano, ...  
4  Basmetto, Cantalupa, Case Nuove, Chiaravalle, ...  
5  Arzaga, Barona, Boffalora, Cascina Bianca, Con...  
6  Assiano, Baggio, Figino, Fopponino, Forze Arma...  
7  Boldinasco, Bullona, Cagnola, Campo dei Fiori,...  
8  Affori, Bicocca, Bovisa, Bovisasca, Bruzzano, ...

In [8]:
def split_df_rows_for_comma_separated_key(key, df):
    df=df.set_index(df.columns.drop(key,1).tolist())[key].str.split(',', expand=True).stack().reset_index().rename(columns={0:key}).loc[:, df.columns]
    df=df[df[key] != '']
    return df

In [10]:
ml_df2 = split_df_rows_for_comma_separated_key('Neighborhood', ml_df1)

# Remove the blank space at the beginning of the neighborhood names
ml_df2['Neighborhood'] = ml_df2['Neighborhood'].str.strip()

print(ml_df2.shape)
ml_df2.head(10)

(145, 2)


Borough        Neighborhood
0                                     Centro storico               Brera
1                                     Centro storico      Centro Storico
2                                     Centro storico  Conca del Naviglio
3                                     Centro storico           Guastalla
4                                     Centro storico      Porta Sempione
5                                     Centro storico      Porta Tenaglia
6  Stazione Centrale, Gorla, Turro, Greco, Cresce...             Adriano
7  Stazione Centrale, Gorla, Turro, Greco, Cresce...         Crescenzago
8  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Gorla
9  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Greco

In [13]:
geolocator = Nominatim(user_agent = 'myGeocoder')

# Conveneint function to delay between geocoding calls
geocode = RateLimiter(geolocator.geocode, min_delay_seconds=1)

ml_df2['Location'] = ml_df2['Neighborhood'] + ', Milan'
# ml_df2['Location'] = ml_df2['Neighborhood']

ml_df2['gcode'] = ml_df2.Location.apply(geolocator.geocode)

ml_df2['Latitude'] = [g.latitude for g in ml_df2.gcode]
ml_df2['Longitude'] = [g.longitude for g in ml_df2.gcode]

ml_df3 = ml_df2.drop(['Location', 'gcode'], axis = 1)

print(ml_df3.shape)
ml_df3.head(10)

(145, 4)


Borough        Neighborhood  \
0                                     Centro storico               Brera   
1                                     Centro storico      Centro Storico   
2                                     Centro storico  Conca del Naviglio   
3                                     Centro storico           Guastalla   
4                                     Centro storico      Porta Sempione   
5                                     Centro storico      Porta Tenaglia   
6  Stazione Centrale, Gorla, Turro, Greco, Cresce...             Adriano   
7  Stazione Centrale, Gorla, Turro, Greco, Cresce...         Crescenzago   
8  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Gorla   
9  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Greco   

    Latitude  Longitude  
0  45.473479   9.188408  
1  45.447112   9.094054  
2  45.458560   9.177745  
3  45.458252   9.200023  
4  45.477128   9.170598  
5  45.477821   9.181593  
6  45.513572   9.251202  
7  45.509219   9.247484  
8  45.504945   9.224539  
9  45.502184   9.211233

In [57]:
# Made corrections to eliminate outliers based on generating the below map of Milan and observing outliers which are presumed to be due
# which are presumed to be due to innaccurate geospatial coordinates for a few neighborhoods.

lon_correction1 = ml_df3[(ml_df3['Longitude'] > 9.3)].index
ml_df4 = ml_df3.drop(lon_correction1)

lon_correction2 = ml_df4[(ml_df4['Longitude'] < 9.05)].index
ml_df4.drop(lon_correction2, inplace = True)

lat_correction1 = ml_df4[(ml_df4['Latitude'] < 45.3)].index
ml_df4.drop(lat_correction1, inplace = True)

lat_correction2 = ml_df4[(ml_df4['Latitude'] > 45.6)].index
ml_df4.drop(lat_correction2, inplace = True)

ml_df4.index = range(len(ml_df4.index))

print(ml_df4.shape)
ml_df4.head(10)

(136, 4)


Borough        Neighborhood  \
0                                     Centro storico               Brera   
1                                     Centro storico      Centro Storico   
2                                     Centro storico  Conca del Naviglio   
3                                     Centro storico           Guastalla   
4                                     Centro storico      Porta Sempione   
5                                     Centro storico      Porta Tenaglia   
6  Stazione Centrale, Gorla, Turro, Greco, Cresce...             Adriano   
7  Stazione Centrale, Gorla, Turro, Greco, Cresce...         Crescenzago   
8  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Gorla   
9  Stazione Centrale, Gorla, Turro, Greco, Cresce...               Greco   

    Latitude  Longitude  
0  45.473479   9.188408  
1  45.447112   9.094054  
2  45.458560   9.177745  
3  45.458252   9.200023  
4  45.477128   9.170598  
5  45.477821   9.181593  
6  45.513572   9.251202  
7  45.509219   9.247484  
8  45.504945   9.224539  
9  45.502184   9.211233

In [15]:
# Use geopy library to get the latitude and longitude values of Milan

address = 'Milan, Italy'

geolocator = Nominatim(user_agent="mil_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Milan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Milan are 45.4668, 9.1905.


In [18]:
# create map of Milan with the neighborhoods superimposed on it using latitude and longitude values  
map_milan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(ml_df4['Latitude'], ml_df4['Longitude'], ml_df4['Borough'], ml_df4['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_milan)  
    
map_milan

Define Foursquare Credentials and Version

In [19]:
# The code was removed by Watson Studio for sharing.

In [22]:
# The code was removed by Watson Studio for sharing.

In [23]:
# function that extracts the category of the venue

def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [25]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

C:\Users\shive\anaconda3\envs\IBM Classes\lib\site-packages\ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name             categories        lat       lng
0    Pinacoteca di Brera             Art Museum  45.471979  9.188128
1         Palazzo Parigi                  Hotel  45.473378  9.191108
2       Palazzo di Brera  College Arts Building  45.472019  9.188043
3  Hops Beer Shop Milano             Beer Store  45.475240  9.189126
4                SUSHI B    Japanese Restaurant  45.472153  9.186883

In [26]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

98 venues were returned by Foursquare.


In [36]:
# The code was removed by Watson Studio for sharing.

In [29]:
print(milan_venues.shape)
milan_venues.head(10)

(3759, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0        Brera              45.473479                9.188408   
1        Brera              45.473479                9.188408   
2        Brera              45.473479                9.188408   
3        Brera              45.473479                9.188408   
4        Brera              45.473479                9.188408   
5        Brera              45.473479                9.188408   
6        Brera              45.473479                9.188408   
7        Brera              45.473479                9.188408   
8        Brera              45.473479                9.188408   
9        Brera              45.473479                9.188408   

                    Venue  Venue Latitude  Venue Longitude  \
0     Pinacoteca di Brera       45.471979         9.188128   
1          Palazzo Parigi       45.473378         9.191108   
2        Palazzo di Brera       45.472019         9.188043   
3   Hops Beer Shop Milano       45.475240         9.189126   
4                 SUSHI B       45.472153         9.186883   
5           Dimore Studio       45.474770         9.186954   
6        Osteria di Brera       45.472207         9.187045   
7  Di Viole Di Liquirizia       45.471460         9.185336   
8  Orto Botanico di Brera       45.471197         9.189577   
9    BVLGARI Hotel Milano       45.470149         9.189318   

          Venue Category  
0             Art Museum  
1                  Hotel  
2  College Arts Building  
3             Beer Store  
4    Japanese Restaurant  
5            Art Gallery  
6     Italian Restaurant  
7           Cupcake Shop  
8       Botanical Garden  
9                  Hotel

In [30]:
milan_venues.groupby('Neighborhood').count().head(10)

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                         
Acquabella                        7                       7      7   
Adriano                           8                       8      8   
Affori                           16                      16     16   
Arzaga                           22                      22     22   
Assiano                           2                       2      2   
Baggio                           10                      10     10   
Barona                            7                       7      7   
Bicocca                          38                      38     38   
Boffalora                         8                       8      8   
Boldinasco                       21                      21     21   

              Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                   
Acquabella                 7                7               7  
Adriano                    8                8               8  
Affori                    16               16              16  
Arzaga                    22               22              22  
Assiano                    2                2               2  
Baggio                    10               10              10  
Barona                     7                7               7  
Bicocca                   38               38              38  
Boffalora                  8                8               8  
Boldinasco                21               21              21

In [31]:
print('There are {} uniques categories.'.format(len(milan_venues['Venue Category'].unique())))

There are 298 uniques categories.


### Toronto, Canada

The Toronto dataframe containing the neighborhood information and geospatial coordinates was already created for a previous project for this course therefore instead of recreating it, the magic store command will be utilized to bring the dataframe from its original notebook into this notebook.

In [32]:
%store -r WT3

print(WT3.shape)
WT3.head(10)

(103, 5)


City           Borough                                 Neighborhood  \
0  Toronto        North York                                    Parkwoods   
1  Toronto        North York                             Victoria Village   
2  Toronto  Downtown Toronto                    Regent Park, Harbourfront   
3  Toronto        North York             Lawrence Manor, Lawrence Heights   
4  Toronto  Downtown Toronto  Queen's Park, Ontario Provincial Government   
5  Toronto         Etobicoke      Islington Avenue, Humber Valley Village   
6  Toronto       Scarborough                               Malvern, Rouge   
7  Toronto        North York                                    Don Mills   
8  Toronto         East York              Parkview Hill, Woodbine Gardens   
9  Toronto  Downtown Toronto                     Garden District, Ryerson   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494  
5  43.667856 -79.532242  
6  43.806686 -79.194353  
7  43.745906 -79.352188  
8  43.706397 -79.309937  
9  43.657162 -79.378937

In [34]:
# Use geopy library to get the latitude and longitude values of Toronto

address = 'Toronto'

geolocator = Nominatim(user_agent="tor_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [35]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(WT3['Latitude'], WT3['Longitude'], WT3['Borough'], WT3['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [37]:
print(toronto_venues.shape)
toronto_venues.head()

(2167, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2  Victoria Village              43.725882              -79.315572   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude  \
0         Brookbanks Park       43.751976       -79.332140   
1           Variety Store       43.751974       -79.333114   
2  Victoria Village Arena       43.723481       -79.315635   
3             Tim Hortons       43.725517       -79.313103   
4               Portugril       43.725819       -79.312785   

          Venue Category  
0                   Park  
1      Food & Drink Shop  
2           Hockey Arena  
3            Coffee Shop  
4  Portuguese Restaurant

In [38]:
toronto_venues.groupby('Neighborhood').count().head(10)

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  7   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      22   
Berczy Park                                                            55   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           25   
Business reply mail Processing Centre, South Ce...                     16   
CN Tower, King and Spadina, Railway Lands, Harb...                     17   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Agincourt                                                                5   
Alderwood, Long Branch                                                   7   
Bathurst Manor, Wilson Heights, Downsview North                         21   
Bayview Village                                                          4   
Bedford Park, Lawrence Manor East                                       22   
Berczy Park                                                             55   
Birch Cliff, Cliffside West                                              4   
Brockton, Parkdale Village, Exhibition Place                            25   
Business reply mail Processing Centre, South Ce...                      16   
CN Tower, King and Spadina, Railway Lands, Harb...                      17   

                                                    Venue  Venue Latitude  \
Neighborhood                                                                
Agincourt                                               5               5   
Alderwood, Long Branch                                  7               7   
Bathurst Manor, Wilson Heights, Downsview North        21              21   
Bayview Village                                         4               4   
Bedford Park, Lawrence Manor East                      22              22   
Berczy Park                                            55              55   
Birch Cliff, Cliffside West                             4               4   
Brockton, Parkdale Village, Exhibition Place           25              25   
Business reply mail Processing Centre, South Ce...     16              16   
CN Tower, King and Spadina, Railway Lands, Harb...     17              17   

                                                    Venue Longitude  \
Neighborhood                                                          
Agincourt                                                         5   
Alderwood, Long Branch                                            7   
Bathurst Manor, Wilson Heights, Downsview North                  21   
Bayview Village                                                   4   
Bedford Park, Lawrence Manor East                                22   
Berczy Park                                                      55   
Birch Cliff, Cliffside West                                       4   
Brockton, Parkdale Village, Exhibition Place                     25   
Business reply mail Processing Centre, South Ce...               16   
CN Tower, King and Spadina, Railway Lands, Harb...               17   

                                                    Venue Category  
Neighborhood                                                        
Agincourt                                                        5  
Alderwood, Long Branch                                           7  
Bathurst Manor, Wilson Heights, Downsview North                 21  
Bayview Village                                                  4 

In [39]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 277 uniques categories.


### New York City, USA

The New York City dataframe containing the neighborhood information and geospatial coordinates was already created for a previous project for this course therefore instead of recreating it, the magic store command will be utilized to bring the dataframe from its original notebook into this notebook.

In [40]:
%store -r NYC_df

print(NYC_df.shape)
NYC_df.head(10)

(306, 5)


City    Borough    Neighborhood   Latitude  Longitude
0  New York City      Bronx       Wakefield  40.894705 -73.847201
1  New York City      Bronx      Co-op City  40.874294 -73.829939
2  New York City      Bronx     Eastchester  40.887556 -73.827806
3  New York City      Bronx       Fieldston  40.895437 -73.905643
4  New York City      Bronx       Riverdale  40.890834 -73.912585
5  New York City      Bronx     Kingsbridge  40.881687 -73.902818
6  New York City  Manhattan     Marble Hill  40.876551 -73.910660
7  New York City      Bronx        Woodlawn  40.898273 -73.867315
8  New York City      Bronx         Norwood  40.877224 -73.879391
9  New York City      Bronx  Williamsbridge  40.881039 -73.857446

In [41]:
# Use geopy library to get the latitude and longitude values of New York City

address = 'New York City'

geolocator = Nominatim(user_agent="nyc_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [42]:
# create map of New York City using latitude and longitude values
map_nyc = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(NYC_df['Latitude'], NYC_df['Longitude'], NYC_df['Borough'], NYC_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_nyc)  
    
map_nyc

In [43]:
print(NYC_venues.shape)
NYC_venues.head()

(10478, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3           Dunkin'       40.890459       -73.849089      Donut Shop  
4  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop

In [44]:
NYC_venues.groupby('Neighborhood').count().head(10)

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                            
Allerton                            34                      34     34   
Annadale                            12                      12     12   
Arden Heights                        6                       6      6   
Arlington                            7                       7      7   
Arrochar                            24                      24     24   
Arverne                             21                      21     21   
Astoria                            100                     100    100   
Astoria Heights                     13                      13     13   
Auburndale                          20                      20     20   
Bath Beach                          46                      46     46   

                 Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                      
Allerton                     34               34              34  
Annadale                     12               12              12  
Arden Heights                 6                6               6  
Arlington                     7                7               7  
Arrochar                     24               24              24  
Arverne                      21               21              21  
Astoria                     100              100             100  
Astoria Heights              13               13              13  
Auburndale                   20               20              20  
Bath Beach                   46               46              46

In [45]:
print('There are {} uniques categories.'.format(len(NYC_venues['Venue Category'].unique())))

There are 436 uniques categories.


## Methodology <a name="methodology"></a>

The goal of this project is to identify neighborhoods and their corresponding commercial venue profiles for Milan neighborhoods where Italian restaurants are located and then to identify similar neighborhoods in Toronto, Canada and New York City, USA.  Once **the subset of neighborhoods that meet these general characteristics** are identified, it will be **further analyzed** via data from Foursquare to discover the neighborhoods with the most prevalent data **for supporting upscale Italian restaurants.**

The Data section detailed the collection and wrangling of data that forms the foundation for the rest of this project.  The work described in the Analysis section will combine this data from multiple independent sources to provide meaningfil insights and recommendations.  As was the case in the Data section, the Analysis section will be segmented for work with each of the individual cities as much as possible then concatenated for the final analysis.

The work in the Analys section will follow an ordered process:
1. Build a **dataframe** for each city populated with the **commercial venue information for each neighborhood.**  
2. Concatenate these dataframes into **one master neighborhood venue dataframe** and to similarly concatenate individual city data to build a **master neighborhood locaton dataframe.**
3. Work with the master dataframes and **k-Means Clustering to build** a new combined master **dataframe** that lists the **ranked top ten commercial venue types for each neighborhood and subdivides the neighborhoods into clusters based on their commercial venue profiles.**  **Silhouette analysis** will be applied to the data in order **to identify the best k to utilize during the final k-Means Clustering.** in order to provide the most meaningful analysis.
4. Analyze this combined master dataframe to **identify the subset of Toronto and New York City neighborhoods** that are most promising for future expansion.  
5. **Final analysis** of the subset of neighborhoods to **identify the top neighborhoods most appropriate for supporting the upscale-style of Italian restaurant featured by the chain.**  This will be accomplished by utilizing the Foursquare API to find all Italian restaurants with a price tier of 4 (highest average price for an entree) in the subset neighborhoods.

## Analysis <a name="analysis"></a>

### 1) Milan Dataframe

In [66]:
# one hot encoding
milan_onehot = pd.get_dummies(milan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
milan_onehot['Neighborhood'] = milan_venues['Neighborhood'] 

# move neighborhood column to the first column
nb2 = milan_onehot['Neighborhood']
milan_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
milan_onehot.insert(0, 'Neighborhood', nb2)

print(milan_onehot.shape)
milan_onehot.head()

(3759, 298)


Neighborhood  Abruzzo Restaurant  Accessories Store  Adult Education Center  \
0        Brera                   0                  0                       0   
1        Brera                   0                  0                       0   
2        Brera                   0                  0                       0   
3        Brera                   0                  0                       0   
4        Brera                   0                  0                       0   

   African Restaurant  Airport  Airport Service  American Restaurant  \
0                   0        0                0                    0   
1                   0        0                0                    0   
2                   0        0                0                    0   
3                   0        0                0                    0   
4                   0        0                0                    0   

   Amphitheater  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0             0         0       0                       0            0   
1             0         0       0                       0            0   
2             0         0       0                       0            0   
3             0         0       0                       0            0   
4             0         0       0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           1                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Australian Restaurant  Automotive Shop  BBQ Joint  \
0                   0                      0                0          0   
1                   0                      0                0          0   
2                   0                      0                0          0   
3                   0                      0                0          0   
4                   0                      0                0          0   

   Bagel Shop  Bakery  Ballroom  Bar  Basketball Court  Bed & Breakfast  \
0           0       0         0    0                 0                0   
1           0       0         0    0                 0                0   
2           0       0         0    0                 0                0   
3           0       0         0    0                 0                0   
4           0       0         0    0                 0                0   

   Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  Bike Shop  Bistro  \
0         0            0           0                   0          0       0   
1         0            0           0                   0          0       0   
2         0            0           0                   0          0       0   
3         0            0           1                   0          0       0   
4         0            0           0                   0          0       0   

   Board Shop  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0           0          0                 0         0              0   
1           0          0                 0         0              0   
2           0          0                 0         0              0   
3           0          0                 0         0              0   
4           0          0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0          

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [47]:
milan_grouped = milan_onehot.groupby('Neighborhood').mean().reset_index()

milan_grouped.shape
milan_grouped.head(10)

Neighborhood  Abruzzo Restaurant  Accessories Store  Adult Education Center  \
0   Acquabella                 0.0                0.0                     0.0   
1      Adriano                 0.0                0.0                     0.0   
2       Affori                 0.0                0.0                     0.0   
3       Arzaga                 0.0                0.0                     0.0   
4      Assiano                 0.0                0.0                     0.0   
5       Baggio                 0.0                0.0                     0.0   
6       Barona                 0.0                0.0                     0.0   
7      Bicocca                 0.0                0.0                     0.0   
8    Boffalora                 0.0                0.0                     0.0   
9   Boldinasco                 0.0                0.0                     0.0   

   African Restaurant  Airport  Airport Service  American Restaurant  \
0                 0.0      0.0              0.0                  0.0   
1                 0.0      0.0              0.0                  0.0   
2                 0.0      0.0              0.0                  0.0   
3                 0.0      0.0              0.0                  0.0   
4                 0.0      0.0              0.0                  0.0   
5                 0.0      0.0              0.0                  0.0   
6                 0.0      0.0              0.0                  0.0   
7                 0.0      0.0              0.0                  0.0   
8                 0.0      0.0              0.0                  0.0   
9                 0.0      0.0              0.0                  0.0   

   Amphitheater  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0           0.0       0.0     0.0                     0.0          0.0   
1           0.0       0.0     0.0                     0.0          0.0   
2           0.0       0.0     0.0                     0.0          0.0   
3           0.0       0.0     0.0                     0.0          0.0   
4           0.0       0.0     0.0                     0.0          0.0   
5           0.0       0.0     0.0                     0.0          0.0   
6           0.0       0.0     0.0                     0.0          0.0   
7           0.0       0.0     0.0                     0.0          0.0   
8           0.0       0.0     0.0                     0.0          0.0   
9           0.0       0.0     0.0                     0.0          0.0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0         0.0                  0.0                   0.0               0.0   
1         0.0                  0.0                   0.0               0.0   
2         0.0                  0.0                   0.0               0.0   
3         0.0                  0.0                   0.0               0.0   
4         0.0                  0.0                   0.0               0.0   
5         0.0                  0.0                   0.0               0.0   
6         0.0                  0.0                   0.0               0.0   
7         0.0                  0.0                   0.0               0.0   
8         0.0                  0.0                   0.0               0.0   
9         0.0                  0.0                   0.0               0.0   

   Athletics & Sports  Australian Restaurant  Automotive Shop  BBQ Joint  \
0            0.000000                    0.0              0.0        0.0   
1            0.000000                    0.0              0.0        0.0   
2            0.000000                    0.0              0.0        0.0   
3            0.045455                    0.0              0.0        0.0   
4            0.000000                    0.0              0.0        0.0   
5            0.000000                    0.0              0.0        0.0   
6            0.142857                    0.0              0.0        0.0   
7            0.000000              

In [49]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]



Now let's create a new dataframe and display the top 10 venues for each neighborhood.

In [69]:
# num_top_venues = 10

# indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
# columns = ['Neighborhood']
# for ind in np.arange(num_top_venues):
#     try:
#         columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
#     except:
#         columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
# milan_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
# milan_neighborhoods_venues_sorted['Neighborhood'] = milan_grouped['Neighborhood']

# for ind in np.arange(milan_grouped.shape[0]):
#     milan_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(milan_grouped.iloc[ind, :], num_top_venues)

# The total size of this project's notebook grew to over 52 MB which is above the size allowed to be uploaded IBM
# Watson Studio Cloud thus to limit this notebook to an allowable size I have commented out the code in order to show
# my work however I am loading the resultant dataframe from another notebook where I completed the background work

%store -r milan_neighborhoods_venues_sorted

print(milan_neighborhoods_venues_sorted.shape)
milan_neighborhoods_venues_sorted.head(10)

(134, 11)


Neighborhood     1st Most Common Venue 2nd Most Common Venue  \
0   Acquabella      Fast Food Restaurant   Sporting Goods Shop   
1      Adriano        Italian Restaurant        Ice Cream Shop   
2       Affori                      Café    Italian Restaurant   
3       Arzaga               Pizza Place            Playground   
4      Assiano  Mediterranean Restaurant            Restaurant   
5       Baggio                      Café     Convenience Store   
6       Barona                   Dog Run    Athletics & Sports   
7      Bicocca                      Café    Italian Restaurant   
8    Boffalora              Soccer Field                Bakery   
9   Boldinasco              Tram Station                 Hotel   

    3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0  Furniture / Home Store        Warehouse Store                   Pub   
1            Soccer Field  Performing Arts Venue     Trattoria/Osteria   
2             Pizza Place           Cocktail Bar                  Park   
3                    Café    Japanese Restaurant        Cosmetics Shop   
4       Fish & Chips Shop    Empanada Restaurant           Event Space   
5                   Plaza                Dog Run             Gastropub   
6                    Café      Trattoria/Osteria          Soccer Field   
7             Pizza Place             Restaurant                 Plaza   
8      Athletics & Sports                   Café     Trattoria/Osteria   
9              Restaurant                 Bakery    Italian Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Flower Shop        Hardware Store           Yoga Studio   
1      Toy / Game Store       Cultural Center     Fish & Chips Shop   
2              Pharmacy   Fried Chicken Joint             Pool Hall   
3            Food Court           Supermarket              Pharmacy   
4    Falafel Restaurant                  Farm        Farmers Market   
5           Supermarket                   Bar   Japanese Restaurant   
6               Theater           Yoga Studio  Fast Food Restaurant   
7      Sushi Restaurant                   Pub            Piadineria   
8               Dog Run               Theater           Yoga Studio   
9    Chinese Restaurant             Gun Range    Seafood Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Event Space     Falafel Restaurant  
1           Event Space     Falafel Restaurant  
2                  Pool      Health Food Store  
3    Athletics & Sports   Gym / Fitness Center  
4  Fast Food Restaurant    Filipino Restaurant  
5    Italian Restaurant                   Food  
6    Falafel Restaurant                   Farm  
7          College Quad         Sandwich Place  
8  Fast Food Restaurant     Falafel Restaurant  
9                  Café                    Bar

In [58]:
# The code was removed by Watson Studio for sharing.

In [62]:
# The code was removed by Watson Studio for sharing.

In [63]:
ml_df5.head()

City         Borough        Neighborhood   Latitude  Longitude
0  Milan  Centro storico               Brera  45.473479   9.188408
1  Milan  Centro storico      Centro Storico  45.447112   9.094054
2  Milan  Centro storico  Conca del Naviglio  45.458560   9.177745
3  Milan  Centro storico           Guastalla  45.458252   9.200023
4  Milan  Centro storico      Porta Sempione  45.477128   9.170598

### 1) Toronto Dataframe

Since the previous work from the prior assignement limited the neighborhood analysis to only boroughs that contained the word "Toronto" it is not applicable to this project which is analyzing all Toronto neighborhoods.  Therefore a new neighborhood analysis will be run here.

In [65]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
nb = toronto_onehot['Neighborhood']
toronto_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
toronto_onehot.insert(0, 'Neighborhood', nb)

print(toronto_onehot.shape)
toronto_onehot.head()

(2167, 277)


Neighborhood  Accessories Store  Afghan Restaurant  Airport  \
0         Parkwoods                  0                  0        0   
1         Parkwoods                  0                  0        0   
2  Victoria Village                  0                  0        0   
3  Victoria Village                  0                  0        0   
4  Victoria Village                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auto Garage  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0              0          0           0           0       0   
1            0              0          0           0           0       0   
2            0              0          0           0           0       0   
3            0              0          0           0           0       0   
4            0              0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0     0    0               0                 0                   0      0   
1     0    0               0                 0                   0      0   
2     0    0               0                 0                   0      0   
3     0    0               0                 0                   0      0   
4     0    0               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0       0              0          0         0              0   
1       0              0          0         0              0   
2       0              0          0         0              0   
3       0              0          0         0              0   
4       0              0          0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [67]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()

print(toronto_grouped.shape)
toronto_grouped.head(10)

(96, 277)


Neighborhood  Accessories Store  \
0                                          Agincourt                0.0   
1                             Alderwood, Long Branch                0.0   
2    Bathurst Manor, Wilson Heights, Downsview North                0.0   
3                                    Bayview Village                0.0   
4                  Bedford Park, Lawrence Manor East                0.0   
5                                        Berczy Park                0.0   
6                        Birch Cliff, Cliffside West                0.0   
7       Brockton, Parkdale Village, Exhibition Place                0.0   
8  Business reply mail Processing Centre, South C...                0.0   
9  CN Tower, King and Spadina, Railway Lands, Har...                0.0   

   Afghan Restaurant   Airport  Airport Food Court  Airport Gate  \
0                0.0  0.000000            0.000000      0.000000   
1                0.0  0.000000            0.000000      0.000000   
2                0.0  0.000000            0.000000      0.000000   
3                0.0  0.000000            0.000000      0.000000   
4                0.0  0.000000            0.000000      0.000000   
5                0.0  0.000000            0.000000      0.000000   
6                0.0  0.000000            0.000000      0.000000   
7                0.0  0.000000            0.000000      0.000000   
8                0.0  0.000000            0.000000      0.000000   
9                0.0  0.058824            0.058824      0.058824   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0        0.000000         0.000000          0.000000             0.000000   
1        0.000000         0.000000          0.000000             0.000000   
2        0.000000         0.000000          0.000000             0.000000   
3        0.000000         0.000000          0.000000             0.000000   
4        0.000000         0.000000          0.000000             0.045455   
5        0.000000         0.000000          0.000000             0.000000   
6        0.000000         0.000000          0.000000             0.000000   
7        0.000000         0.000000          0.000000             0.000000   
8        0.000000         0.000000          0.000000             0.000000   
9        0.117647         0.117647          0.058824             0.000000   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0           0.0       0.0     0.000000         0.0                  0.0   
1           0.0       0.0     0.000000         0.0                  0.0   
2           0.0       0.0     0.000000         0.0                  0.0   
3           0.0       0.0     0.000000         0.0                  0.0   
4           0.0       0.0     0.000000         0.0                  0.0   
5           0.0       0.0     0.018182         0.0                  0.0   
6           0.0       0.0     0.000000         0.0                  0.0   
7           0.0       0.0     0.000000         0.0                  0.0   
8           0.0       0.0     0.000000         0.0                  0.0   
9           0.0       0.0     0.000000         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0               0.0                 0.0          0.0         0.0000   
1               0.0                 0.0          0.0         0.0000   
2               0.0                 0.0          0.0         0.0000   
3               0.0                 0.0          0.0         0.0000   
4               0.0                 0.0          0.0         0.0000   
5               0.0                 0.0          0.0         0.0000   
6               0.0                 0.0          0.0         0.0000   
7               0.0                 0.0          0.0         0.0000   
8               0.0                 0.0          0.0         0.0625   
9               0.0                 0.0          0.0         0.0000   

   BBQ Jo

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [70]:
# num_top_venues = 10

# indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
# columns = ['Neighborhood']
# for ind in np.arange(num_top_venues):
#    try:
#        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
#    except:
#        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
# toronto_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
# toronto_neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

# for ind in np.arange(toronto_grouped.shape[0]):
#     toronto_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

# %store toronto_neighborhoods_venues_sorted
# toronto_neighborhoods_venues_sorted.head()

# The total size of this project's notebook grew to over 52 MB which is above the size allowed to be uploaded IBM
# Watson Studio Cloud thus to limit this notebook to an allowable size I have commented out the code in order to show
# my work however I am loading the resultant dataframe from another notebook where I completed the background work

%store -r toronto_neighborhoods_venues_sorted

print(toronto_neighborhoods_venues_sorted.shape)
toronto_neighborhoods_venues_sorted.head(10)

(96, 11)


Neighborhood 1st Most Common Venue  \
0                                          Agincourt                Lounge   
1                             Alderwood, Long Branch           Pizza Place   
2    Bathurst Manor, Wilson Heights, Downsview North           Coffee Shop   
3                                    Bayview Village   Japanese Restaurant   
4                  Bedford Park, Lawrence Manor East        Sandwich Place   
5                                        Berczy Park           Coffee Shop   
6                        Birch Cliff, Cliffside West       College Stadium   
7       Brockton, Parkdale Village, Exhibition Place                  Café   
8  Business reply mail Processing Centre, South C...           Pizza Place   
9  CN Tower, King and Spadina, Railway Lands, Har...        Airport Lounge   

   2nd Most Common Venue      3rd Most Common Venue 4th Most Common Venue  \
0         Breakfast Spot  Latin American Restaurant          Skating Rink   
1         Sandwich Place                Coffee Shop                   Pub   
2                   Bank                   Pharmacy         Deli / Bodega   
3                   Café                       Bank    Chinese Restaurant   
4     Italian Restaurant                Coffee Shop      Greek Restaurant   
5             Restaurant                     Bakery          Cocktail Bar   
6  General Entertainment               Skating Rink                  Café   
7         Breakfast Spot                  Nightclub           Coffee Shop   
8          Auto Workshop              Garden Center                Garden   
9        Airport Service                   Boutique         Historic Site   

  5th Most Common Venue 6th Most Common Venue    7th Most Common Venue  \
0        Clothing Store  Ethiopian Restaurant              Event Space   
1              Pharmacy                   Gym         Greek Restaurant   
2         Shopping Mall           Bridal Shop           Sandwich Place   
3   Distribution Center              Dive Bar                  Dog Run   
4       Thai Restaurant          Liquor Store  Comfort Food Restaurant   
5              Beer Bar        Farmers Market              Cheese Shop   
6            Donut Shop        Discount Store      Distribution Center   
7                   Gym          Climbing Gym            Burrito Place   
8  Fast Food Restaurant    Light Rail Station           Farmers Market   
9                   Bar           Coffee Shop            Boat or Ferry   

  8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
0           Escape Room     Electronics Store             Discount Store  
1        Discount Store      Department Store               Dessert Shop  
2                 Diner            Restaurant  Middle Eastern Restaurant  
3      Doner Restaurant            Donut Shop                Yoga Studio  
4             Juice Bar               Butcher                       Café  
5    Seafood Restaurant        Sandwich Place                      Beach  
6              Dive Bar               Dog Run           Doner Restaurant  
7             Bookstore               Stadium                 Restaurant  
8            Comic Shop                  Park           Recording Studio  
9                 Plane       Harbor / Marina        Rental Car Location

### 1) New York City Dataframe

Since the previous work from the prior assignement limited the neighborhood analysis to only neighborohoods in the Manhattan borough it is not applicable to this project which is analyzing all New York City neighborhoods in all five boroughs. Therefore a new neighborhood analysis will be run here.

In [71]:
# one hot encoding
NYC_onehot = pd.get_dummies(NYC_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
NYC_onehot['Neighborhood'] = NYC_venues['Neighborhood'] 

# move neighborhood column to the first column
nb7 = NYC_onehot['Neighborhood']
NYC_onehot.drop(labels=['Neighborhood'], axis=1,inplace = True)
NYC_onehot.insert(0, 'Neighborhood', nb7)

print(NYC_onehot.shape)
NYC_onehot.head()

(10478, 436)


Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Wakefield                  0               0                  0   
1    Wakefield                  0               0                  0   
2    Wakefield                  0               0                  0   
3    Wakefield                  0               0                  0   
4    Wakefield                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Garage  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0                0          0           0           0       0   
1            0                0          0           0           0       0   
2            0                0          0           0           0       0   
3            0                0          0           0           0       0   
4            0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0          0                0         0            0           0   
1      0          0                0         0            0           0   
2      0          0                0         0            0           0   
3      0          0                0         0            0           0   
4      0          0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0          

Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [72]:
NYC_grouped = NYC_onehot.groupby('Neighborhood').mean().reset_index()

print(NYC_grouped.shape)
NYC_grouped.head(10)

(302, 436)


Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0         Allerton                0.0             0.0                0.0   
1         Annadale                0.0             0.0                0.0   
2    Arden Heights                0.0             0.0                0.0   
3        Arlington                0.0             0.0                0.0   
4         Arrochar                0.0             0.0                0.0   
5          Arverne                0.0             0.0                0.0   
6          Astoria                0.0             0.0                0.0   
7  Astoria Heights                0.0             0.0                0.0   
8       Auburndale                0.0             0.0                0.0   
9       Bath Beach                0.0             0.0                0.0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                 0.0               0.0             0.000000           0.0   
1                 0.0               0.0             0.166667           0.0   
2                 0.0               0.0             0.000000           0.0   
3                 0.0               0.0             0.000000           0.0   
4                 0.0               0.0             0.000000           0.0   
5                 0.0               0.0             0.000000           0.0   
6                 0.0               0.0             0.000000           0.0   
7                 0.0               0.0             0.000000           0.0   
8                 0.0               0.0             0.050000           0.0   
9                 0.0               0.0             0.000000           0.0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0     0.0               0.0                     0.0     0.029412         0.0   
1     0.0               0.0                     0.0     0.000000         0.0   
2     0.0               0.0                     0.0     0.000000         0.0   
3     0.0               0.0                     0.0     0.000000         0.0   
4     0.0               0.0                     0.0     0.000000         0.0   
5     0.0               0.0                     0.0     0.000000         0.0   
6     0.0               0.0                     0.0     0.000000         0.0   
7     0.0               0.0                     0.0     0.000000         0.0   
8     0.0               0.0                     0.0     0.000000         0.0   
9     0.0               0.0                     0.0     0.000000         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0          0.000000   
1                  0.0                   0.0          0.000000   
2                  0.0                   0.0          0.000000   
3                  0.0                   0.0          0.000000   
4                  0.0                   0.0          0.000000   
5                  0.0                   0.0          0.000000   
6                  0.0                   0.0          0.000000   
7                  0.0                   0.0          0.000000   
8                  0.0                   0.0          0.000000   
9                  0.0                   0.0          0.021739   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0            0.000000         0.0                    0.0                  0.0   
1            0.000000         0.0                    0.0                  0.0   
2            0.000000         0.0                    0.0                  0.0   
3            0.000000         0.0                    0.0                  0.0   
4            0.041667         0.0                    0.0                  0.0   
5            0.000000         0.0                    0.0                  0.0   
6            0.000000         0.0                    0.0                  0.0   
7            0.000000         0.0                    0

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [73]:
# num_top_venues = 10

# indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
# columns = ['Neighborhood']
# for ind in np.arange(num_top_venues):
#     try:
#         columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
#     except:
#         columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
# NYC_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
# NYC_neighborhoods_venues_sorted['Neighborhood'] = NYC_grouped['Neighborhood']

# for ind in np.arange(NYC_grouped.shape[0]):
#     NYC_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(NYC_grouped.iloc[ind, :], num_top_venues)

# %store NYC_neighborhoods_venues_sorted
# NYC_neighborhoods_venues_sorted.head()

# The total size of this project's notebook grew to over 52 MB which is above the size allowed to be uploaded IBM
# Watson Studio Cloud thus to limit this notebook to an allowable size I have commented out the code in order to show
# my work however I am loading the resultant dataframe from another notebook where I completed the background work

%store -r NYC_neighborhoods_venues_sorted

print(NYC_neighborhoods_venues_sorted.shape)
NYC_neighborhoods_venues_sorted.head(10)

(302, 11)


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Allerton           Pizza Place    Chinese Restaurant   
1         Annadale           Pizza Place   American Restaurant   
2    Arden Heights              Pharmacy         Deli / Bodega   
3        Arlington         Grocery Store               Gay Bar   
4         Arrochar         Deli / Bodega              Bus Stop   
5          Arverne             Surf Spot         Metro Station   
6          Astoria            Hookah Bar                   Bar   
7  Astoria Heights                 Plaza    Chinese Restaurant   
8       Auburndale    Italian Restaurant     Mobile Phone Shop   
9       Bath Beach    Italian Restaurant           Gas Station   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Deli / Bodega                   Spa            Playground   
1              Train Station            Bagel Shop                  Park   
2                 Smoke Shop           Coffee Shop              Bus Stop   
3              Boat or Ferry          Home Service              Bus Stop   
4         Italian Restaurant    Athletics & Sports            Food Truck   
5             Sandwich Place            Playground         Burrito Place   
6  Middle Eastern Restaurant    Seafood Restaurant                Bakery   
7                Pizza Place            Playground         Bowling Alley   
8                 Hookah Bar    Miscellaneous Shop      Toy / Game Store   
9                Pizza Place            Donut Shop              Pharmacy   

  6th Most Common Venue  7th Most Common Venue      8th Most Common Venue  \
0           Supermarket    Martial Arts School                     Bakery   
1                  Food             Restaurant               Dance Studio   
2           Pizza Place            Fish Market                    Factory   
3           Coffee Shop          Deli / Bodega       Fast Food Restaurant   
4           Supermarket  Outdoors & Recreation  Middle Eastern Restaurant   
5            Restaurant        Thai Restaurant                Coffee Shop   
6     Indian Restaurant            Pizza Place                 Food Truck   
7                Bakery             Laundromat                     Hostel   
8    Athletics & Sports             Comic Shop           Sushi Restaurant   
9    Chinese Restaurant   Fast Food Restaurant       Cantonese Restaurant   

      9th Most Common Venue 10th Most Common Venue  
0         Electronics Store  Outdoors & Recreation  
1             Deli / Bodega                  Diner  
2        Falafel Restaurant                   Farm  
3            Farmers Market                   Food  
4  Mediterranean Restaurant                    Bar  
5                Board Shop            Pizza Place  
6  Mediterranean Restaurant       Greek Restaurant  
7                      Food            Supermarket  
8                  Pharmacy                    Bar  
9           Bubble Tea Shop           Dessert Shop

### 2) Master Neighborhood Venue Dataframe

In [75]:
# total_grouped = pd.concat([milan_grouped, toronto_grouped, NYC_grouped], ignore_index=True)
# total_grouped

# total_grouped = total_grouped.fillna(0.000000)

# The total size of this project's notebook grew to over 52 MB which is above the size allowed to be uploaded IBM
# Watson Studio Cloud thus to limit this notebook to an allowable size I have commented out the code in order to show
# my work however I am loading the resultant dataframe from another notebook where I completed the background work

%store -r total_grouped

print(total_grouped.shape)
total_grouped.head(10)

(532, 503)


Neighborhood  Abruzzo Restaurant  Accessories Store  Adult Education Center  \
0   Acquabella                 0.0                0.0                     0.0   
1      Adriano                 0.0                0.0                     0.0   
2       Affori                 0.0                0.0                     0.0   
3       Arzaga                 0.0                0.0                     0.0   
4      Assiano                 0.0                0.0                     0.0   
5       Baggio                 0.0                0.0                     0.0   
6       Barona                 0.0                0.0                     0.0   
7      Bicocca                 0.0                0.0                     0.0   
8    Boffalora                 0.0                0.0                     0.0   
9   Boldinasco                 0.0                0.0                     0.0   

   African Restaurant  Airport  Airport Service  American Restaurant  \
0                 0.0      0.0              0.0                  0.0   
1                 0.0      0.0              0.0                  0.0   
2                 0.0      0.0              0.0                  0.0   
3                 0.0      0.0              0.0                  0.0   
4                 0.0      0.0              0.0                  0.0   
5                 0.0      0.0              0.0                  0.0   
6                 0.0      0.0              0.0                  0.0   
7                 0.0      0.0              0.0                  0.0   
8                 0.0      0.0              0.0                  0.0   
9                 0.0      0.0              0.0                  0.0   

   Amphitheater  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0           0.0       0.0     0.0                     0.0          0.0   
1           0.0       0.0     0.0                     0.0          0.0   
2           0.0       0.0     0.0                     0.0          0.0   
3           0.0       0.0     0.0                     0.0          0.0   
4           0.0       0.0     0.0                     0.0          0.0   
5           0.0       0.0     0.0                     0.0          0.0   
6           0.0       0.0     0.0                     0.0          0.0   
7           0.0       0.0     0.0                     0.0          0.0   
8           0.0       0.0     0.0                     0.0          0.0   
9           0.0       0.0     0.0                     0.0          0.0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0         0.0                  0.0                   0.0               0.0   
1         0.0                  0.0                   0.0               0.0   
2         0.0                  0.0                   0.0               0.0   
3         0.0                  0.0                   0.0               0.0   
4         0.0                  0.0                   0.0               0.0   
5         0.0                  0.0                   0.0               0.0   
6         0.0                  0.0                   0.0               0.0   
7         0.0                  0.0                   0.0               0.0   
8         0.0                  0.0                   0.0               0.0   
9         0.0                  0.0                   0.0               0.0   

   Athletics & Sports  Australian Restaurant  Automotive Shop  BBQ Joint  \
0            0.000000                    0.0              0.0        0.0   
1            0.000000                    0.0              0.0        0.0   
2            0.000000                    0.0              0.0        0.0   
3            0.045455                    0.0              0.0        0.0   
4            0.000000                    0.0              0.0        0.0   
5            0.000000                    0.0              0.0        0.0   
6            0.142857                    0.0              0.0        0.0   
7            0.000000              

### 2) Master Neighborhood Locaton Dataframe

In [76]:
total_coord = ml_df5.append(WT3, ignore_index = True)

In [77]:
total_coord = total_coord.append(NYC_df, ignore_index = True)

In [80]:
total_coord.head(10)

City                                            Borough  \
0  Milan                                     Centro storico   
1  Milan                                     Centro storico   
2  Milan                                     Centro storico   
3  Milan                                     Centro storico   
4  Milan                                     Centro storico   
5  Milan                                     Centro storico   
6  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
7  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
8  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
9  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   

         Neighborhood   Latitude  Longitude  
0               Brera  45.473479   9.188408  
1      Centro Storico  45.447112   9.094054  
2  Conca del Naviglio  45.458560   9.177745  
3           Guastalla  45.458252   9.200023  
4      Porta Sempione  45.477128   9.170598  
5      Porta Tenaglia  45.477821   9.181593  
6             Adriano  45.513572   9.251202  
7         Crescenzago  45.509219   9.247484  
8               Gorla  45.504945   9.224539  
9               Greco  45.502184   9.211233

In [81]:
total_coord.drop(index = 45, axis = 0, inplace = True)
total_coord.drop(index = 140, axis = 0, inplace = True)
total_coord.drop(index = 187, axis = 0, inplace = True)
total_coord.drop(index = 230, axis = 0, inplace = True)

total_coord.index = range(len(total_coord.index))

total_coord.head(10)

City                                            Borough  \
0  Milan                                     Centro storico   
1  Milan                                     Centro storico   
2  Milan                                     Centro storico   
3  Milan                                     Centro storico   
4  Milan                                     Centro storico   
5  Milan                                     Centro storico   
6  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
7  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
8  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
9  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   

         Neighborhood   Latitude  Longitude  
0               Brera  45.473479   9.188408  
1      Centro Storico  45.447112   9.094054  
2  Conca del Naviglio  45.458560   9.177745  
3           Guastalla  45.458252   9.200023  
4      Porta Sempione  45.477128   9.170598  
5      Porta Tenaglia  45.477821   9.181593  
6             Adriano  45.513572   9.251202  
7         Crescenzago  45.509219   9.247484  
8               Gorla  45.504945   9.224539  
9               Greco  45.502184   9.211233

### 3) k-Means Clustering with Silhouette Analysis

In [84]:
# Silhouette Analysis is performed to determine the optimum value for k

sil = []
kmax = 10

total_grouped_clustering = total_grouped.drop('Neighborhood', 1)

# dissimilarity would not be defined for a single cluster, thus, minimum number of clusters should be 2
for k in range(3, kmax+1):
  kmeans_total = KMeans(n_clusters = k, random_state = 0).fit(total_grouped_clustering)
  labels = kmeans_total.labels_
  sil.append(silhouette_score(total_grouped_clustering, labels, metric = 'euclidean'))

sil

[0.031105065148005373,
 0.04306070456186652,
 0.04811349246296942,
 0.04485577408704314,
 0.05036572256509973,
 0.05665548349149245,
 0.06316349162819809,
 0.04227498429296539]

The values for silhouette analysis can range from -1 to 1 with the higher the number the more optimum the k value.  In our analysis a k value of 9 has the highest value of 0.063 therefore that will be the value for k in our k-Means Clustering.  As a sidebar, the relatively low values obtained during the silhouette analysis indicate that the data does not fit well into very segmented clusters which is to be expected with the commercial venue categories data.

In [85]:
# Performing the final k-Means Clustering

# set number of clusters
k = 9

# run k-means clustering
kmeans_total = KMeans(n_clusters = k, random_state = 0).fit(total_grouped_clustering)

kmeans_total.labels_[0:10]

array([3, 1, 1, 0, 3, 1, 1, 1, 1, 1])

### 3) Combined Master Dataframe

In [91]:
total_neighborhoods_venues_sorted = milan_neighborhoods_venues_sorted.append(toronto_neighborhoods_venues_sorted, ignore_index = True)

In [92]:
total_neighborhoods_venues_sorted = total_neighborhoods_venues_sorted.append(NYC_neighborhoods_venues_sorted, ignore_index = True)

print(total_neighborhoods_venues_sorted.shape)
total_neighborhoods_venues_sorted.head(10)

(532, 11)


Neighborhood     1st Most Common Venue 2nd Most Common Venue  \
0   Acquabella      Fast Food Restaurant   Sporting Goods Shop   
1      Adriano        Italian Restaurant        Ice Cream Shop   
2       Affori                      Café    Italian Restaurant   
3       Arzaga               Pizza Place            Playground   
4      Assiano  Mediterranean Restaurant            Restaurant   
5       Baggio                      Café     Convenience Store   
6       Barona                   Dog Run    Athletics & Sports   
7      Bicocca                      Café    Italian Restaurant   
8    Boffalora              Soccer Field                Bakery   
9   Boldinasco              Tram Station                 Hotel   

    3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
0  Furniture / Home Store        Warehouse Store                   Pub   
1            Soccer Field  Performing Arts Venue     Trattoria/Osteria   
2             Pizza Place           Cocktail Bar                  Park   
3                    Café    Japanese Restaurant        Cosmetics Shop   
4       Fish & Chips Shop    Empanada Restaurant           Event Space   
5                   Plaza                Dog Run             Gastropub   
6                    Café      Trattoria/Osteria          Soccer Field   
7             Pizza Place             Restaurant                 Plaza   
8      Athletics & Sports                   Café     Trattoria/Osteria   
9              Restaurant                 Bakery    Italian Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Flower Shop        Hardware Store           Yoga Studio   
1      Toy / Game Store       Cultural Center     Fish & Chips Shop   
2              Pharmacy   Fried Chicken Joint             Pool Hall   
3            Food Court           Supermarket              Pharmacy   
4    Falafel Restaurant                  Farm        Farmers Market   
5           Supermarket                   Bar   Japanese Restaurant   
6               Theater           Yoga Studio  Fast Food Restaurant   
7      Sushi Restaurant                   Pub            Piadineria   
8               Dog Run               Theater           Yoga Studio   
9    Chinese Restaurant             Gun Range    Seafood Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0           Event Space     Falafel Restaurant  
1           Event Space     Falafel Restaurant  
2                  Pool      Health Food Store  
3    Athletics & Sports   Gym / Fitness Center  
4  Fast Food Restaurant    Filipino Restaurant  
5    Italian Restaurant                   Food  
6    Falafel Restaurant                   Farm  
7          College Quad         Sandwich Place  
8  Fast Food Restaurant     Falafel Restaurant  
9                  Café                    Bar

In [93]:
# add clustering labels
total_neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans_total.labels_)

# neighborhoods_venues_sorted
total_merged = total_coord

# merge milan_grouped with ml_df5 to add latitude/longitude for each neighborhood
total_merged = total_merged.join(total_neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

print(total_merged.shape)
total_merged.head(10)

(538, 16)


City                                            Borough  \
0  Milan                                     Centro storico   
1  Milan                                     Centro storico   
2  Milan                                     Centro storico   
3  Milan                                     Centro storico   
4  Milan                                     Centro storico   
5  Milan                                     Centro storico   
6  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
7  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
8  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   
9  Milan  Stazione Centrale, Gorla, Turro, Greco, Cresce...   

         Neighborhood   Latitude  Longitude  Cluster Labels  \
0               Brera  45.473479   9.188408               1   
1      Centro Storico  45.447112   9.094054               1   
2  Conca del Naviglio  45.458560   9.177745               1   
3           Guastalla  45.458252   9.200023               1   
4      Porta Sempione  45.477128   9.170598               1   
5      Porta Tenaglia  45.477821   9.181593               1   
6             Adriano  45.513572   9.251202               1   
7         Crescenzago  45.509219   9.247484               1   
8               Gorla  45.504945   9.224539               1   
9               Greco  45.502184   9.211233               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0    Italian Restaurant        Ice Cream Shop                 Hotel   
1                   Bar           Pizza Place    Italian Restaurant   
2    Italian Restaurant                  Café        Ice Cream Shop   
3    Italian Restaurant          Tram Station           Pizza Place   
4    Italian Restaurant           Pizza Place          Cocktail Bar   
5    Italian Restaurant   Japanese Restaurant                  Café   
6    Italian Restaurant        Ice Cream Shop          Soccer Field   
7    Italian Restaurant                  Café        Ice Cream Shop   
8    Italian Restaurant           Pizza Place                 Hotel   
9           Supermarket    Seafood Restaurant    Chinese Restaurant   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0    Japanese Restaurant                  Café           Pizza Place   
1                   Park         Shopping Mall          Cupcake Shop   
2            Pizza Place          Cocktail Bar    Seafood Restaurant   
3         Ice Cream Shop            Restaurant      Kebab Restaurant   
4    Japanese Restaurant        Ice Cream Shop                Bakery   
5     Chinese Restaurant        Ice Cream Shop           Pizza Place   
6  Performing Arts Venue     Trattoria/Osteria      Toy / Game Store   
7               Bus Stop         Metro Station           Supermarket   
8                  Plaza                  Park                   Spa   
9                   Café                 Hotel                 Plaza   

  7th Most Common Venue     8th Most Common Venue 9th Most Common Venue  \
0            Restaurant              Cocktail Bar        Sandwich Place   
1   Fried Chicken Joint             Movie Theater                  Food   
2                Bistro                       Pub            Restaurant   
3                   Bar                  Wine Bar          Cocktail Bar   
4             Gastropub  Mediterranean Restaurant                   Gym   
5              Wine Bar          Sushi Restaurant        Sandwich Place   
6       Cultural Center         Fish & Chips Shop           Event Space   
7              Pharmacy    Furniture / Home Store     Trattoria/Osteria   
8               Brewery              Cocktail Bar           Coffee Shop   
9             Pet Store               Coffee Shop          Cocktail Bar   

  10th Most Common Venue  
0           Dessert Shop  
1                 Lounge  
2               Boutique  
3                 Bakery  
4           Dessert Shop  
5           Tram Station  
6     Falafel Restaurant  

### 4) Combined Master Dataframe Analysis to Identify Neighborhoods That are Most Promising for Future Expansion

Visualize the Clusters

Maps of the three cities showing the distribution of the neighborhoods in clusters

In [99]:
# Milan map

address = 'Milan, Italy'

geolocator = Nominatim(user_agent="mil_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

map_clusters_total = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(k)
ys = [i + x + (i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(total_merged['Latitude'], total_merged['Longitude'], total_merged['Neighborhood'], total_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_total)
       

print('Milan Map')    
map_clusters_total

Milan Map


In [101]:
# Toronto map

address = 'Toronto'

geolocator = Nominatim(user_agent="tor_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

map_clusters_total = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(k)
ys = [i + x + (i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(total_merged['Latitude'], total_merged['Longitude'], total_merged['Neighborhood'], total_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_total)
       

print('Toronto Map')    
map_clusters_total

Toronto Map


In [102]:
# New York City map

address = 'New York City'

geolocator = Nominatim(user_agent="nyc_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

map_clusters_total = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(k)
ys = [i + x + (i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(total_merged['Latitude'], total_merged['Longitude'], total_merged['Neighborhood'], total_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_total)
       

print('New York City Map')    
map_clusters_total

New York City Map


Examine the Clusters

In [103]:
# Summarizing the neighborhoods in each cluster and city

pd.crosstab(total_merged['Cluster Labels'], total_merged['City'], margins = True, margins_name = 'Total')

City            Milan  New York City  Toronto  Total
Cluster Labels                                      
0                  14             25       11     50
1                  91             13        4    108
2                   0              3        5      8
3                  26            258       71    355
4                   0              0        2      2
5                   0              0        1      1
6                   0              0        1      1
7                   2              6        2     10
8                   0              2        1      3
Total             133            307       98    538

In [104]:
# Summarizing the percentage of each city's nieghborhoods in each cluster

pd.crosstab(total_merged['Cluster Labels'], total_merged['City'], normalize = 'columns')

City               Milan  New York City   Toronto
Cluster Labels                                   
0               0.105263       0.081433  0.112245
1               0.684211       0.042345  0.040816
2               0.000000       0.009772  0.051020
3               0.195489       0.840391  0.724490
4               0.000000       0.000000  0.020408
5               0.000000       0.000000  0.010204
6               0.000000       0.000000  0.010204
7               0.015038       0.019544  0.020408
8               0.000000       0.006515  0.010204

Cluster 0

In [105]:
total_merged.loc[total_merged['Cluster Labels'] == 0, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                                       Neighborhood  \
27           Milan                                            Rottole   
36           Milan                                         Morsenchio   
44           Milan                                            Taliedo   
52           Milan                                          Morivione   
62           Milan                                             Arzaga   
82           Milan                                       Forze Armate   
104          Milan                                            Musocco   
107          Milan                                     Quarto Oggiaro   
111          Milan                                             Trenno   
122          Milan                                           Comasina   
123          Milan                                            Dergano   
128          Milan                                           Niguarda   
131          Milan                                    Prato Centenaro   
132          Milan                                            Segnano   
134        Toronto                                   Victoria Village   
139        Toronto                    Parkview Hill, Woodbine Gardens   
141        Toronto                                          Glencairn   
148        Toronto  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
181        Toronto                                      Humber Summit   
199        Toronto                                          Westmount   
201        Toronto                        Willowdale, Willowdale West   
206        Toronto  Kingsview Village, St. Phillips, Martin Grove ...   
211        Toronto            Clarks Corners, Tam O'Shanter, Sullivan   
218        Toronto  South Steeles, Silverstone, Humbergate, Jamest...   
222        Toronto                             Alderwood, Long Branch   
238  New York City                                            Norwood   
244  New York City                                 University Heights   
245  New York City                                     Morris Heights   
247  New York City                                       East Tremont   
250  New York City                                            Melrose   
262  New York City                                           Van Nest   
263  New York City                                        Morris Park   
266  New York City                                    North Riverdale   
268  New York City                                      Schuylerville   
270  New York City                                        Castle Hill   
310  New York City                                       Borough Park   
322  New York City                                            Midwood   
328  New York City                                      Ocean Parkway   
374  New York City                                           Glendale   
411  New York City                                        Floral Park   
435  New York City                                      Port Richmond   
438  New York City                                  Castleton Corners   
444  New York City                                        Eltingville   
445  New York City                                           Annadale   
470  New York City                                          Rossville   
471  New York City                                      Arden Heights   
473  New York City                                  Heartland Village   
486  New York City                                      Randall Manor   
500  New York City                                         Mount Hope   
521  New York City                                       Prince's Bay   

     Cluster Labels 1st Most Common Venue   2nd Most Common Venue  \
27                0           Pizza Place                     Bar   
36                0           Pizza Place             Supermarket   
44                0           Pizza Place                  Garden   
52            

Cluster 0 is comprised of roughly equal percentage (8-10%) of the neighborhoods in each of Milan, Toronto, and New York City.  Most of the neighborhoods have pizza places as the most common type of venue.

Cluster 1

In [106]:
total_merged.loc[total_merged['Cluster Labels'] == 1, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                    Neighborhood  Cluster Labels  \
0            Milan                           Brera               1   
1            Milan                  Centro Storico               1   
2            Milan              Conca del Naviglio               1   
3            Milan                       Guastalla               1   
4            Milan                  Porta Sempione               1   
5            Milan                  Porta Tenaglia               1   
6            Milan                         Adriano               1   
7            Milan                     Crescenzago               1   
8            Milan                           Gorla               1   
10           Milan                          Loreto               1   
11           Milan                      Maggiolina               1   
12           Milan                       Mirabello               1   
13           Milan                    Ponte Seveso               1   
14           Milan                     Porta Nuova               1   
15           Milan                        Precotto               1   
16           Milan               Stazione Centrale               1   
17           Milan                           Turro               1   
18           Milan       Villaggio dei Giornalisti               1   
19           Milan                       Casoretto               1   
20           Milan                         Cimiano               1   
22           Milan                        Lambrate               1   
23           Milan                          Ortica               1   
24           Milan                  Porta Monforte               1   
25           Milan                   Porta Venezia               1   
29           Milan                      Calvairate               1   
30           Milan                      Castagnedo               1   
31           Milan                        Cavriano               1   
33           Milan                      Gamboloita               1   
35           Milan                          Monluè               1   
37           Milan                          Nosedo               1   
38           Milan                           Omero               1   
39           Milan                    Ponte Lambro               1   
40           Milan                  Porta Vittoria               1   
41           Milan                    Porta Romana               1   
42           Milan                        Rogoredo               1   
43           Milan                       San Luigi               1   
45           Milan                     Chiaravalle               1   
46           Milan                    Chiesa Rossa               1   
47           Milan                   Conca Fallata               1   
48           Milan                     Gratosoglio               1   
49           Milan                     Le Terrazze               1   
51           Milan                       Missaglia               1   
53           Milan                  Porta Lodovica               1   
54           Milan                 Porta Vigentina               1   
55           Milan                      Quintosole               1   
57           Milan                      Selvanesco               1   
58           Milan                         Stadera               1   
60           Milan                    Vaiano Valle               1   
63           Milan                          Barona               1   
64           Milan                       Boffalora               1   
65           Milan                       Conchetta               1   
66           Milan                           Creta               1   
67           Milan                        Foppette               1   
68           Milan         Giambellino-Lorenteggio               1   
69           Milan                Lodovico il Moro               1   
70           Milan                    Porta Genova               1   
71           Milan      

Cluster 1 is largely Milan-centric.  Roughly 68% of the Milan neighborhoods are in this cluster while only around 4% of the neighborhoods for both Toronto and New York City are in this cluster.  Most of the neighborhoods have Italian restuarants as the most common type of venue.  **This is the cluster that we were hoping to find that is comprised of the Toronto and New York City neighborhoods that are similar to Milan and proven to support Italian restaurants.**

Cluster 2

In [107]:
total_merged.loc[total_merged['Cluster Labels'] == 2, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City         Neighborhood  Cluster Labels 1st Most Common Venue  \
133        Toronto            Parkwoods               2                  Park   
152        Toronto  Caledonia-Fairbanks               2                  Park   
193        Toronto               Weston               2                  Park   
195        Toronto      York Mills West               2                  Park   
220        Toronto             Rosedale               2                  Park   
399  New York City             Rosedale               2                  Park   
422  New York City           Somerville               2                  Park   
433  New York City            Todt Hill               2                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
133     Food & Drink Shop           Yoga Studio             Drugstore   
152         Women's Store                  Pool             Drugstore   
193           Yoga Studio             Drugstore        Discount Store   
195     Convenience Store           Yoga Studio             Drugstore   
220                 Trail            Playground          Tennis Court   
399                 Trail            Playground          Tennis Court   
422           Yoga Studio           Flower Shop               Factory   
433           Yoga Studio           Flower Shop               Factory   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
133        Discount Store   Distribution Center              Dive Bar   
152        Discount Store   Distribution Center              Dive Bar   
193   Distribution Center              Dive Bar               Dog Run   
195        Discount Store   Distribution Center              Dive Bar   
220            Donut Shop                 Diner        Discount Store   
399            Donut Shop                 Diner        Discount Store   
422    Falafel Restaurant                  Farm        Farmers Market   
433    Falafel Restaurant                  Farm        Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
133               Dog Run      Doner Restaurant             Donut Shop  
152               Dog Run      Doner Restaurant             Donut Shop  
193      Doner Restaurant            Donut Shop    Dumpling Restaurant  
195               Dog Run      Doner Restaurant             Donut Shop  
220   Distribution Center              Dive Bar                Dog Run  
399   Distribution Center              Dive Bar                Dog Run  
422  Fast Food Restaurant                 Field    Filipino Restaurant  
433  Fast Food Restaurant                 Field    Filipino Restaurant

Cluster 2 is small with only 8 total neighborhoods.  Milan has no neighborhoods in this cluster while roughly 1% of New York City neighborhoods are in this cluster along with around 5% of the Toronto neighborhoods.  The neighborhoods in this cluster appear to be lower income with parks being the most common type of venue and discount stores and dive bars featured priminently in the top ten most common types of venues.

Cluster 3

In [108]:
total_merged.loc[total_merged['Cluster Labels'] == 3, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                                       Neighborhood  \
9            Milan                                              Greco   
21           Milan                                        Città Studi   
26           Milan                                   Quartiere Feltre   
28           Milan                                         Acquabella   
32           Milan                                          Forlanini   
34           Milan                                          La Trecca   
50           Milan                                          Macconago   
56           Milan                               Ronchetto delle Rane   
59           Milan                                           Torretta   
61           Milan                                          Vigentino   
78           Milan                                            Assiano   
80           Milan                                             Figino   
83           Milan                                              Harar   
84           Milan                                       La Maddalena   
85           Milan                                           Muggiano   
89           Milan                                      Quinto Romano   
90           Milan                                           San Siro   
91           Milan                                           Valsesia   
92           Milan                                         Vercellese   
99           Milan                                              Fiera   
100          Milan                                        Gallaratese   
109          Milan                                            Roserio   
110          Milan                                       San Leonardo   
120          Milan                                         Ca' Granda   
124          Milan                                       Fulvio Testi   
126          Milan                                         La Fontana   
135        Toronto                          Regent Park, Harbourfront   
136        Toronto                   Lawrence Manor, Lawrence Heights   
137        Toronto        Queen's Park, Ontario Provincial Government   
140        Toronto                           Garden District, Ryerson   
142        Toronto  West Deane Park, Princess Gardens, Martin Grov...   
144        Toronto                                          Don Mills   
145        Toronto                                   Woodbine Heights   
146        Toronto                                     St. James Town   
147        Toronto                                 Humewood-Cedarvale   
149        Toronto                  Guildwood, Morningside, West Hill   
150        Toronto                                        The Beaches   
151        Toronto                                        Berczy Park   
153        Toronto                                             Woburn   
154        Toronto                                            Leaside   
155        Toronto                                 Central Bay Street   
157        Toronto                                          Cedarbrae   
158        Toronto                                  Hillcrest Village   
159        Toronto    Bathurst Manor, Wilson Heights, Downsview North   
160        Toronto                                   Thorncliffe Park   
161        Toronto                           Richmond, Adelaide, King   
162        Toronto                       Dufferin, Dovercourt Village   
163        Toronto                                Scarborough Village   
164        Toronto                       Fairview, Henry Farm, Oriole   
165        Toronto                    Northwood Park, York University   
166        Toronto      East Toronto, Broadview North (Old East York)   
167        Toronto  Harbourfront East, Union Station, Toronto Islands   
168        Toronto                           Little Portugal, Trinity   
169        Toronto        Kennedy Park, Ionview, East Birchmount Park   

Cluster 3 is the largest cluster.  It is more heavily populated with New York City and Toronto neighborhoods.  20% of the Milan neighborhoods are in this cluster along with roughly 84% of the New York City neighborhoods and 72% of the Toronto neighborhoods. 

Cluster 4

In [109]:
total_merged.loc[total_merged['Cluster Labels'] == 4, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                                       Neighborhood  \
186  Toronto                                   Humberlea, Emery   
228  Toronto  Old Mill South, King's Mill Park, Sunnylea, Hu...   

     Cluster Labels       1st Most Common Venue 2nd Most Common Venue  \
186               4              Baseball Field           Yoga Studio   
228               4  Construction & Landscaping        Baseball Field   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
186   Dumpling Restaurant              Dive Bar               Dog Run   
228           Yoga Studio   Dumpling Restaurant              Dive Bar   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
186      Doner Restaurant            Donut Shop             Drugstore   
228               Dog Run      Doner Restaurant            Donut Shop   

           9th Most Common Venue       10th Most Common Venue  
186  Eastern European Restaurant               Discount Store  
228                    Drugstore  Eastern European Restaurant

Cluster 4 is a small cluster comprised solely of roughly 2% of the Toronto neighborhoods.  It features baseball fields along with dive bars, drugstores, and international dining venues.  

Cluster 5

In [110]:
total_merged.loc[total_merged['Cluster Labels'] == 5, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City              Neighborhood  Cluster Labels 1st Most Common Venue  \
176  Toronto  York Mills, Silver Hills               5   Martial Arts School   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
176           Yoga Studio             Drugstore        Discount Store   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
176   Distribution Center              Dive Bar               Dog Run   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
176      Doner Restaurant            Donut Shop    Dumpling Restaurant

Cluster 5 is comprised of a single Toronto neighborhood which means it has 1% of the Toronto neighborhoods.  It appears to be a lower income, strip mall neighborhood.

Cluster 6

In [111]:
total_merged.loc[total_merged['Cluster Labels'] == 6, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City    Neighborhood  Cluster Labels 1st Most Common Venue  \
138  Toronto  Malvern, Rouge               6  Fast Food Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
138           Yoga Studio             Drugstore        Discount Store   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
138   Distribution Center              Dive Bar               Dog Run   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
138      Doner Restaurant            Donut Shop    Dumpling Restaurant

Cluster 6 is comprised of a single Toronto neighborhood which means it has 1% of the Toronto neighborhoods.  It appears to be a lower income neighborhood.

Cluster 7

In [112]:
total_merged.loc[total_merged['Cluster Labels'] == 7, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                            Neighborhood  Cluster Labels  \
87           Milan                    Quartiere degli Olmi               7   
113          Milan                                  Vialba               7   
143        Toronto  Rouge Hill, Port Union, Highland Creek               7   
223        Toronto     Northwest, West Humber - Clairville               7   
239  New York City                          Williamsbridge               7   
378  New York City                        South Ozone Park               7   
423  New York City                              Brookville               7   
432  New York City                             Grymes Hill               7   
437  New York City                              Port Ivory               7   
442  New York City                                 Oakwood               7   

          1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
87                 Soccer Field                   Bar     Food & Drink Shop   
113                Soccer Field         Historic Site                   Bar   
143  Construction & Landscaping                   Bar           Yoga Studio   
223               Garden Center   Rental Car Location                   Bar   
239                   Nightclub         Deli / Bodega                   Bar   
378                        Park                   Bar        Sandwich Place   
423               Deli / Bodega      Recording Studio           Yoga Studio   
432               Deli / Bodega               Dog Run           Yoga Studio   
437                         Bar                  Food               Factory   
442              Nightlife Spot         Women's Store                   Bar   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
87            Yoga Studio    Falafel Restaurant                  Farm   
113                  Park    Falafel Restaurant                  Farm   
143   Dumpling Restaurant              Dive Bar               Dog Run   
223             Drugstore           Yoga Studio      Doner Restaurant   
239            Restaurant  Caribbean Restaurant            Soup Place   
378             Hotel Bar            Donut Shop                  Food   
423                  Food               Factory    Falafel Restaurant   
432     Food & Drink Shop    Falafel Restaurant                  Farm   
437    Falafel Restaurant                  Farm        Farmers Market   
442            Playground                Lawyer                  Food   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
87         Farmers Market  Fast Food Restaurant   Filipino Restaurant   
113        Farmers Market  Fast Food Restaurant   Filipino Restaurant   
143      Doner Restaurant            Donut Shop             Drugstore   
223        Discount Store   Distribution Center              Dive Bar   
239           Flower Shop                  Farm        Farmers Market   
378  Fast Food Restaurant            Food Truck         Deli / Bodega   
423                  Farm        Farmers Market  Fast Food Restaurant   
432        Farmers Market  Fast Food Restaurant                 Field   
437  Fast Food Restaurant                 Field   Filipino Restaurant   
442    Falafel Restaurant                  Farm        Farmers Market   

          10th Most Common Venue  
87             Fish & Chips Shop  
113                  Yoga Studio  
143  Eastern European Restaurant  
223                      Dog Run  
239         Fast Food Restaurant  
378                        Hotel  
423                        Field  
432          Filipino Restaurant  
437            Fish & Chips Shop  
442         Fast Food Restaurant

Cluster 7 is a small cluster with roughly equal percentage (2%) of the neighborhoods in each of Milan, Toronto, and New York City.  It appears to be an entertainment-centric cluster.

Cluster 8

In [113]:
total_merged.loc[total_merged['Cluster Labels'] == 8, total_merged.columns[[0, 2] + list(range(5, total_merged.shape[1]))]]

City                 Neighborhood  Cluster Labels  \
212        Toronto  Moore Park, Summerhill East               8   
311  New York City                Dyker Heights               8   
533  New York City                    Bayswater               8   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
212                 Trail            Playground           Yoga Studio   
311            Playground          Burger Joint            Bagel Shop   
533            Playground           Yoga Studio           Flower Shop   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
212        Discount Store   Distribution Center              Dive Bar   
311           Golf Course         Grocery Store           Flower Shop   
533               Factory    Falafel Restaurant                  Farm   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
212               Dog Run      Doner Restaurant            Donut Shop   
311    Falafel Restaurant                  Farm        Farmers Market   
533        Farmers Market  Fast Food Restaurant                 Field   

    10th Most Common Venue  
212              Drugstore  
311   Fast Food Restaurant  
533    Filipino Restaurant

Cluster 8 is a small cluster with only 1% of the Toronto neighborhoods and 1% of the NYC neighborhoods.  It is an outdoor activity-centric cluster.

### 5) Final Analysis for Identifying the Top Neighborhoods From the Subset For Supporting Upscale Italian Restaurants

Additional analysis is performed on the Cluster 1 neighborhoods.  The Foursquare API is once again utilized to find venues with a category of "Italian Restaurant" and a price tier of 4 (highest average price per entree) in these neighborhoods.

In [114]:
total_merged.loc[total_merged['Cluster Labels'] == 1, total_merged.columns[[0, 2, 3, 4] + list(range(5, total_merged.shape[1]))]]

City                    Neighborhood   Latitude  Longitude  \
0            Milan                           Brera  45.473479   9.188408   
1            Milan                  Centro Storico  45.447112   9.094054   
2            Milan              Conca del Naviglio  45.458560   9.177745   
3            Milan                       Guastalla  45.458252   9.200023   
4            Milan                  Porta Sempione  45.477128   9.170598   
5            Milan                  Porta Tenaglia  45.477821   9.181593   
6            Milan                         Adriano  45.513572   9.251202   
7            Milan                     Crescenzago  45.509219   9.247484   
8            Milan                           Gorla  45.504945   9.224539   
10           Milan                          Loreto  45.484535   9.215276   
11           Milan                      Maggiolina  45.492036   9.201885   
12           Milan                       Mirabello  45.496117   9.199466   
13           Milan                    Ponte Seveso  45.491607   9.206681   
14           Milan                     Porta Nuova  45.479858   9.192694   
15           Milan                        Precotto  45.512651   9.225004   
16           Milan               Stazione Centrale  45.488188   9.208174   
17           Milan                           Turro  45.497513   9.225896   
18           Milan       Villaggio dei Giornalisti  45.499824   9.202561   
19           Milan                       Casoretto  45.488521   9.227395   
20           Milan                         Cimiano  45.501167   9.244620   
22           Milan                        Lambrate  45.483148   9.241998   
23           Milan                          Ortica  45.471260   9.242967   
24           Milan                  Porta Monforte  45.467866   9.207034   
25           Milan                   Porta Venezia  45.474282   9.205226   
29           Milan                      Calvairate  45.456051   9.220625   
30           Milan                      Castagnedo  45.445165   9.231487   
31           Milan                        Cavriano  45.468738   9.241262   
33           Milan                      Gamboloita  45.441315   9.218336   
35           Milan                          Monluè  45.456621   9.254205   
37           Milan                          Nosedo  45.430940   9.224589   
38           Milan                           Omero  45.434453   9.223897   
39           Milan                    Ponte Lambro  45.442841   9.263597   
40           Milan                  Porta Vittoria  45.462261   9.209580   
41           Milan                    Porta Romana  45.452239   9.202056   
42           Milan                        Rogoredo  45.431573   9.244480   
43           Milan                       San Luigi  45.443890   9.214038   
45           Milan                     Chiaravalle  45.416697   9.237421   
46           Milan                    Chiesa Rossa  45.431076   9.176974   
47           Milan                   Conca Fallata  45.424465   9.168241   
48           Milan                     Gratosoglio  45.413160   9.173219   
49           Milan                     Le Terrazze  45.419220   9.178294   
51           Milan                       Missaglia  45.415739   9.171582   
53           Milan                  Porta Lodovica  45.451926   9.187695   
54           Milan                 Porta Vigentina  45.451351   9.196445   
55           Milan                      Quintosole  45.401867   9.204357   
57           Milan                      Selvanesco  45.419290   9.194906   
58           Milan                         Stadera  45.434853   9.179023   
60           Milan                    Vaiano Valle  45.429172   9.215119   
63           Milan                          Barona  45.430724   9.153586   
64           Milan                       Boffalora  45.432353   9.150696   
65           Milan                       Conchetta  45.445473   9.176827   
66           Milan                           Creta  45.457460 

In [147]:
cluster_1_df = total_merged.loc[total_merged['Cluster Labels'] == 1, total_merged.columns[[0, 2, 3, 4]]]

cluster_1_df

City                    Neighborhood   Latitude  Longitude
0            Milan                           Brera  45.473479   9.188408
1            Milan                  Centro Storico  45.447112   9.094054
2            Milan              Conca del Naviglio  45.458560   9.177745
3            Milan                       Guastalla  45.458252   9.200023
4            Milan                  Porta Sempione  45.477128   9.170598
5            Milan                  Porta Tenaglia  45.477821   9.181593
6            Milan                         Adriano  45.513572   9.251202
7            Milan                     Crescenzago  45.509219   9.247484
8            Milan                           Gorla  45.504945   9.224539
10           Milan                          Loreto  45.484535   9.215276
11           Milan                      Maggiolina  45.492036   9.201885
12           Milan                       Mirabello  45.496117   9.199466
13           Milan                    Ponte Seveso  45.491607   9.206681
14           Milan                     Porta Nuova  45.479858   9.192694
15           Milan                        Precotto  45.512651   9.225004
16           Milan               Stazione Centrale  45.488188   9.208174
17           Milan                           Turro  45.497513   9.225896
18           Milan       Villaggio dei Giornalisti  45.499824   9.202561
19           Milan                       Casoretto  45.488521   9.227395
20           Milan                         Cimiano  45.501167   9.244620
22           Milan                        Lambrate  45.483148   9.241998
23           Milan                          Ortica  45.471260   9.242967
24           Milan                  Porta Monforte  45.467866   9.207034
25           Milan                   Porta Venezia  45.474282   9.205226
29           Milan                      Calvairate  45.456051   9.220625
30           Milan                      Castagnedo  45.445165   9.231487
31           Milan                        Cavriano  45.468738   9.241262
33           Milan                      Gamboloita  45.441315   9.218336
35           Milan                          Monluè  45.456621   9.254205
37           Milan                          Nosedo  45.430940   9.224589
38           Milan                           Omero  45.434453   9.223897
39           Milan                    Ponte Lambro  45.442841   9.263597
40           Milan                  Porta Vittoria  45.462261   9.209580
41           Milan                    Porta Romana  45.452239   9.202056
42           Milan                        Rogoredo  45.431573   9.244480
43           Milan                       San Luigi  45.443890   9.214038
45           Milan                     Chiaravalle  45.416697   9.237421
46           Milan                    Chiesa Rossa  45.431076   9.176974
47           Milan                   Conca Fallata  45.424465   9.168241
48           Milan                     Gratosoglio  45.413160   9.173219
49           Milan                     Le Terrazze  45.419220   9.178294
51           Milan                       Missaglia  45.415739   9.171582
53           Milan                  Porta Lodovica  45.451926   9.187695
54           Milan                 Porta Vigentina  45.451351   9.196445
55           Milan                      Quintosole  45.401867   9.204357
57           Milan                      Selvanesco  45.419290   9.194906
58           Milan                         Stadera  45.434853   9.179023
60           Milan                    Vaiano Valle  45.429172   9.215119
63           Milan                          Barona  45.430724   9.153586
64           Milan                       Boffalora  45.432353   9.150696
65           Milan                       Conchetta  45.445473   9.176827
66           Milan                           Creta  45.457460   9.119119
67           Milan                        Foppette  45.450530   9.156451
68           Milan         Giambellino-Lorenteggio  45.446969   9.137871

In [149]:
cluster_1_df2 = cluster_1_df.loc[cluster_1_df['City'] != 'Milan']
cluster_1_df2.index = range(len(cluster_1_df2.index))
cluster_1_df2


City                    Neighborhood   Latitude  Longitude
0         Toronto                        Christie  43.669542 -79.422564
1         Toronto                 Bayview Village  43.786947 -79.385975
2         Toronto     Birch Cliff, Cliffside West  43.692657 -79.264848
3         Toronto  University of Toronto, Harbord  43.662696 -79.400049
4   New York City                         Belmont  40.857277 -73.888452
5   New York City                  Edgewater Park  40.821986 -73.813885
6   New York City               Greenwich Village  40.726933 -73.999914
7   New York City                Mariner's Harbor  40.632546 -74.150085
8   New York City                     Great Kills  40.549480 -74.149324
9   New York City                     Tottenville  40.505334 -74.246569
10  New York City                        Old Town  40.596329 -74.087511
11  New York City                  New Dorp Beach  40.564255 -74.104327
12  New York City                   Richmond Town  40.569606 -74.134057
13  New York City                     Shore Acres  40.609719 -74.066678
14  New York City                        Elm Park  40.630147 -74.141817
15  New York City                     Egbertville  40.579119 -74.127272
16  New York City                 Lighthouse Hill  40.576506 -74.137927

In [187]:
# The code was removed by Watson Studio for sharing.

In [188]:
cluster_1_df2_price_4_Italian_Restaurants = getNearbyVenues(names=cluster_1_df2['Neighborhood'],
                                   latitudes=cluster_1_df2['Latitude'],
                                   longitudes=cluster_1_df2['Longitude']
                                  )

Christie
Bayview Village
Birch Cliff, Cliffside West
University of Toronto, Harbord
Belmont
Edgewater Park
Greenwich Village
Mariner's Harbor
Great Kills
Tottenville
Old Town
New Dorp Beach
Richmond Town
Shore Acres
Elm Park
Egbertville
Lighthouse Hill


In [189]:
print(cluster_1_df2_price_4_Italian_Restaurants.shape)
cluster_1_df2_price_4_Italian_Restaurants

(393, 7)


Neighborhood  Neighborhood Latitude  \
0                          Christie              43.669542   
1                          Christie              43.669542   
2                          Christie              43.669542   
3                          Christie              43.669542   
4                          Christie              43.669542   
5                          Christie              43.669542   
6                          Christie              43.669542   
7                          Christie              43.669542   
8                          Christie              43.669542   
9                          Christie              43.669542   
10                         Christie              43.669542   
11                         Christie              43.669542   
12                         Christie              43.669542   
13                         Christie              43.669542   
14                         Christie              43.669542   
15                         Christie              43.669542   
16                  Bayview Village              43.786947   
17                  Bayview Village              43.786947   
18                  Bayview Village              43.786947   
19                  Bayview Village              43.786947   
20      Birch Cliff, Cliffside West              43.692657   
21      Birch Cliff, Cliffside West              43.692657   
22      Birch Cliff, Cliffside West              43.692657   
23      Birch Cliff, Cliffside West              43.692657   
24   University of Toronto, Harbord              43.662696   
25   University of Toronto, Harbord              43.662696   
26   University of Toronto, Harbord              43.662696   
27   University of Toronto, Harbord              43.662696   
28   University of Toronto, Harbord              43.662696   
29   University of Toronto, Harbord              43.662696   
30   University of Toronto, Harbord              43.662696   
31   University of Toronto, Harbord              43.662696   
32   University of Toronto, Harbord              43.662696   
33   University of Toronto, Harbord              43.662696   
34   University of Toronto, Harbord              43.662696   
35   University of Toronto, Harbord              43.662696   
36   University of Toronto, Harbord              43.662696   
37   University of Toronto, Harbord              43.662696   
38   University of Toronto, Harbord              43.662696   
39   University of Toronto, Harbord              43.662696   
40   University of Toronto, Harbord              43.662696   
41   University of Toronto, Harbord              43.662696   
42   University of Toronto, Harbord              43.662696   
43   University of Toronto, Harbord              43.662696   
44   University of Toronto, Harbord              43.662696   
45   University of Toronto, Harbord              43.662696   
46   University of Toronto, Harbord              43.662696   
47   University of Toronto, Harbord              43.662696   
48   University of Toronto, Harbord              43.662696   
49   University of Toronto, Harbord              43.662696   
50   University of Toronto, Harbord              43.662696   
51   University of Toronto, Harbord              43.662696   
52   University of Toronto, Harbord              43.662696   
53   University of Toronto, Harbord              43.662696   
54   University of Toronto, Harbord              43.662696   
55   University of Toronto, Harbord              43.662696   
56   University of Toronto, Harbord              43.662696   
57   University of Toronto, Harbord              43.662696   
58                          Belmont              40.857277   
59                          Belmont              40.857277   
60                          Belmont              40.857277   
61                          Belmont              40.857277   
62                          Belmont              40.857277   
63                          Belmont              40.857

In [190]:
cluster_1_final_price_4_Italian_Restaurants = cluster_1_df2_price_4_Italian_Restaurants.loc[cluster_1_df2_price_4_Italian_Restaurants['Venue Category'] == 'Italian Restaurant']

print(cluster_1_final_price_4_Italian_Restaurants.shape)
cluster_1_final_price_4_Italian_Restaurants

(54, 7)


Neighborhood  Neighborhood Latitude  \
3                          Christie              43.669542   
27   University of Toronto, Harbord              43.662696   
58                          Belmont              40.857277   
67                          Belmont              40.857277   
72                          Belmont              40.857277   
73                          Belmont              40.857277   
77                          Belmont              40.857277   
78                          Belmont              40.857277   
80                          Belmont              40.857277   
83                          Belmont              40.857277   
86                          Belmont              40.857277   
89                          Belmont              40.857277   
92                          Belmont              40.857277   
93                          Belmont              40.857277   
94                          Belmont              40.857277   
100                         Belmont              40.857277   
107                         Belmont              40.857277   
117                         Belmont              40.857277   
119                         Belmont              40.857277   
143                         Belmont              40.857277   
158                  Edgewater Park              40.821986   
164                  Edgewater Park              40.821986   
165                  Edgewater Park              40.821986   
167                  Edgewater Park              40.821986   
174               Greenwich Village              40.726933   
187               Greenwich Village              40.726933   
190               Greenwich Village              40.726933   
192               Greenwich Village              40.726933   
195               Greenwich Village              40.726933   
206               Greenwich Village              40.726933   
212               Greenwich Village              40.726933   
216               Greenwich Village              40.726933   
223               Greenwich Village              40.726933   
234               Greenwich Village              40.726933   
244               Greenwich Village              40.726933   
275                Mariner's Harbor              40.632546   
277                Mariner's Harbor              40.632546   
284                     Great Kills              40.549480   
294                     Great Kills              40.549480   
306                     Tottenville              40.505334   
310                        Old Town              40.596329   
311                        Old Town              40.596329   
312                        Old Town              40.596329   
315                        Old Town              40.596329   
333                  New Dorp Beach              40.564255   
339                  New Dorp Beach              40.564255   
342                   Richmond Town              40.569606   
345                     Shore Acres              40.609719   
346                     Shore Acres              40.609719   
361                     Shore Acres              40.609719   
375                        Elm Park              40.630147   
380                        Elm Park              40.630147   
383                     Egbertville              40.579119   
389                 Lighthouse Hill              40.576506   

     Neighborhood Longitude  \
3                -79.422564   
27               -79.400049   
58               -73.888452   
67               -73.888452   
72               -73.888452   
73               -73.888452   
77               -73.888452   
78               -73.888452   
80               -73.888452   
83               -73.888452   
86               -73.888452   
89               -73.888452   
92               -73.888452   
93               -73.888452   
94               -73.888452   
100              -73.888452   
107              -73.888452   
117              -73.888452   
119              -73.88

In [191]:
cluster_1_final_price_4_Italian_Restaurants['Neighborhood'].value_counts()

Belmont                           18
Greenwich Village                 11
Old Town                           4
Edgewater Park                     4
Shore Acres                        3
Great Kills                        2
Mariner's Harbor                   2
New Dorp Beach                     2
Elm Park                           2
Richmond Town                      1
University of Toronto, Harbord     1
Egbertville                        1
Christie                           1
Lighthouse Hill                    1
Tottenville                        1
Name: Neighborhood, dtype: int64

This analysis clearly shows that the two New York City neighborhoods of Belmont and Greenwich Village have the highest amount of upscale Italian restaurants in Cluster 1 neighborhoods.

## Results and Discussion <a name="results"></a>

Our analysis identified the following Toronto and New York City neighborhoods subset that are similar to Milan neighborhoods where Italian restaurants thrive:
* **Toronto Neighborhoods**
  1. Christie
  2. Bayview Village
  3. Birch Cliff/Cliffside West
  4. University of Toronto/Harboard
* **New York City Neighborhoods**
  1. Belmont
  2. Edgewater Park
  3. Greenwich Village
  4. Mariner's Harbor
  5. Great Kills
  6. Tottenville
  7. Old Town
  8. New Dorp Beach
  9. Richmond Town
  10. Shore Acres
  11. Elm Park
  12. Egbertville
  13. Lighthouse Hill

The foursquare API was utilized to further analyze this subset by researching which of the member neighborhoods currently support upscale (price tier = 4) Italian restaurants. This analysis determined that the two New York City neighborhoods of Belmont and Greenwich Village contained the vast majority of the upscale (price tier 4) Italian restaurants in the subset.  Thus, Belmont and Greenwich Village are the most promising candidates by following the chain's strategy for future expansion.

## Conclusion <a name="conclusion"></a>

The goal of this project was to identify neighborhoods in Toronto, Canada and New York City, USA that fit the international expansion strategy for an upscale Italian restaurant chain based in Milan, Italy.  The primary focus of this strategy is to identify neighborhoods that have a similar commercial venue profile to the Milan neighborhoods that the chain and other Italian resturants currently operate in. This type of strategy allows the restaurant chain to take a safer approach to international expansion.  Additionally, it also allows the chain to benefit from the "second mover" advantage as it is reveals neighborhoods where it is already proven that Italian restaurants can be successful.

By utilizing neighborhood information from the internet and venue information from the Foursquare API, we were able to apply k-Means Clustering to intelligentally cluster the neighborhoods of the three cities.  This clustering clearly identified a subset of four Toronto neighborhoods and thirteen New York City neighborhoods that are similar to Milan neighborhoods where Italian restaurants thrive.  The foursquare API was utilized to further analyze this subset by researching which of the member neighborhoods currently support upscale (price tier = 4) Italian restaurants.  This analysis determined that the two New York City neighborhoods of Belmont and Greenwich Village are the best fits for future expansion based on the company's international expansion strategy.

Many factors will ultimately go into expansion decisions.  The results of this project are one such factor that provides a data driven direction for stakeholders to consider and further explore.